In [ ]:
!gdown 1W90lq3I_5RY-Ff48hjR3QoqBzHFAxOiR
from google.colab import drive
drive.mount('/content/drive')
!mkdir /content/drive/MyDrive/IDSC

Downloading...
From (original): https://drive.google.com/uc?id=1W90lq3I_5RY-Ff48hjR3QoqBzHFAxOiR
From (redirected): https://drive.google.com/uc?id=1W90lq3I_5RY-Ff48hjR3QoqBzHFAxOiR&confirm=t&uuid=de6dc8fb-25da-415f-bb56-6f3f33f5e931
To: /content/IDSC2025_AnXplore03.zip
100% 1.45G/1.45G [00:14<00:00, 102MB/s]
Mounted at /content/drive
mkdir: cannot create directory ‘/content/drive/MyDrive/IDSC’: File exists


In [ ]:
# !ls
# !unzip /content/IDSC2025_AnXplore03.zip -d /content/drive/MyDrive/IDSC/


In [ ]:
! pip install meshio

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 166.2/166.2 kB 11.3 MB/s eta 0:00:00


In [ ]:
import os
import os.path as osp
import shutil
import meshio
from typing import List

### XDMF ARCHIVE ###
# The dataset simulations are stored in XDMF/HDF5 achives (one .xdmf and one .h5 for each simulation).
# This format allows to compress a whole simulation in 2 files.
# To access the mesh data, or save mesh data to this format, you can use 'xdmf_to_meshes' and 'meshes_to_xdmf'.

def xdmf_to_meshes(xdmf_file_path: str) -> List[meshio.Mesh]:
    """
    Opens an XDMF archive file, and extract a data mesh object for every timestep.

    xdmf_file_path: path to the .xdmf file.
    Returns: list of data mesh objects.
    """

    reader = meshio.xdmf.TimeSeriesReader(xdmf_file_path)
    points, cells = reader.read_points_cells()
    meshes = []

    # Extracting the meshes from the archive
    print("reading from ", reader.num_steps, " steps")
    for i in range(reader.num_steps):
        # Depending on meshio version, the function read_data may return 3 or 4 values.
        try:
            time, point_data, cell_data, _ = reader.read_data(i)
        except ValueError:
            time, point_data, cell_data = reader.read_data(i)
        mesh = meshio.Mesh(points, cells, point_data=point_data, cell_data=cell_data)
        meshes.append(mesh)
    print(f"Loaded {len(meshes)} timesteps from {xdmf_file_path.split('/')[-1]}\n")
    return meshes

def meshes_to_xdmf(
        filename: str,
        meshes: List[meshio.Mesh],
        timestep=1
    ) -> None:
    """
    Writes a time series of meshes (same points and cells) into XDMF/HDF5 archive format.
    The function will write two files: 'filename.xdmf' and 'filename.h5'.

    filename: Chosen name for the archive files.
    meshes: List of meshes to compress, they need to share their cells and points.
    timestep: Timestep betwwen two frames.
    """

    points = meshes[0].points
    cells = meshes[0].cells

    filename = osp.splitext(filename)[0]
    h5_filename = f"{filename}.h5"
    xdmf_filename = f"{filename}.xdmf"

    # Open the TimeSeriesWriter for HDF5
    with meshio.xdmf.TimeSeriesWriter(xdmf_filename) as writer:
        # Write the mesh (points and cells) once
        writer.write_points_cells(points, cells)

        # Loop through time steps and write data
        t = 0
        for mesh in meshes:
            point_data = mesh.point_data
            cell_data = mesh.cell_data
            writer.write_data(t, point_data=point_data, cell_data=cell_data)
            t += timestep

    # The H5 archive is systematically created in cwd, and afterwards moved to the given destination.
    shutil.move(src=osp.join(os.getcwd(), osp.split(h5_filename)[1]), dst=h5_filename)
    print(f"Time series written to {xdmf_filename} and {h5_filename}")


### VTU FILE FORMAT
# A single mesh data object can be stored in a VTU or VTK (.vtu and .vtk).
# Here are the functions to read and save a mesh from a VTU/VTK file.

def vtu_to_mesh(vtu_path: str) -> meshio.Mesh:
    """ Opens a VTU/VTK file and returns a mesh object. """
    return meshio.read(vtu_path)

def mesh_to_vtu(
        mesh: meshio.Mesh,
        vtu_outpath: str
    ) -> None:
    """ Saves a mesh object to a VTU/VTK file. """
    mesh.write(vtu_outpath)
    print(f"Mesh saved to {vtu_outpath}")


### MESHES AND DATA
# The meshio.Mesh object contains the geometry and structure of the mesh, and the associated point and cell data.

def accessing_mesh_data(mesh: meshio.Mesh) -> None:
    """
    Demo function: demonstrates the useful atributes of the Mesh object.
    """

    # POINTS: The positions of the points/nodes of the mesh.
    print(f"There are {mesh.points.shape[0]} nodes in this mesh.")
    print(f"First 5 nodes of the mesh: \n{mesh.points[:5]} \n")

    # CELLS: The cells of the mesh, it shows the connectivity between the nodes.
    print(f"Types of cells in the mesh: {list(mesh.cells_dict)}")
    if "tetra" in mesh.cells_dict:
        print(f"There are {mesh.cells_dict['tetra'].shape[0]} tetrahedral cells in this mesh.")
        print(f"First 5 tetrahedral cells of the mesh: \n{mesh.cells_dict['tetra'][:5]} \n")
    elif "triangle" in mesh.cells_dict:
        print(f"There are {mesh.cells_dict['triangle'].shape[0]} triangular cells in this mesh.")
        print(f"First 5 triangular cells of the mesh: \n{mesh.cells_dict['triangle'][:5]} \n")
    else:
        print("No tetrahedral or triangular cells found in the mesh.")

    # POINT DATA: The data on the mesh points are stored inside the mesh.point_data dictionnary.
    #             This loop prints all the mesh point data features in the mesh, and their shapes.
    for key in mesh.point_data.keys():
        print(f"Feature name: {key} / Feature shape: {mesh.point_data[key].shape}")

def create_mock_mesh() -> meshio.Mesh:
    """ Creates a mock 2D mesh, and saves it to the current directory."""
    points = [
        [0.0, 0.0, 0.0],
        [1.0, 0.0, 0.0],
        [2.0, 0.0, 0.0],
        [0.0, 1.0, 0.0],
        [1.0, 1.0, 0.0],
        [2.0, 1.0, 0.0],
    ]
    cells = [
        ("triangle", [[0, 1, 3], [1, 3, 4], [1, 4, 5], [1, 2, 5]]),
    ]

    mesh = meshio.Mesh(
        points,
        cells,
        # Optionally provide extra data on points, cells, etc.
        point_data={"mock_point_data": [0.0, 1.0, 2.0, 3.0, 4.0, 5.0]},
        cell_data={"mock_cell_data": [[0.0, 1.0, 2.0, 3.0]]},
    )
    print("Mock mesh created.")
    return mesh


In [ ]:

data_dir = "drive/MyDrive/IDSC/4Students_AnXplore03"
from pathlib import Path
data_dir = Path(data_dir)
xdmf_path = data_dir.glob("*.xdmf").__next__()
print(xdmf_path)





drive/MyDrive/IDSC/4Students_AnXplore03/AllFields_Resultats_MESH_129.xdmf


In [ ]:

meshes = xdmf_to_meshes(str(xdmf_path))
print(type(meshes))
accessing_mesh_data(meshes[10])


reading from  80  steps
Loaded 80 timesteps from AllFields_Resultats_MESH_129.xdmf

<class 'list'>
There are 10682 nodes in this mesh.
First 5 nodes of the mesh: 
[[-0.4082757   9.047513   -1.452742  ]
 [-0.49194214  8.805198   -1.5316691 ]
 [-0.58255124  8.53299    -1.5674353 ]
 [-0.70165414  8.311213   -1.5410393 ]
 [-0.8674604   8.095768   -1.478069  ]] 

Types of cells in the mesh: ['tetra']
There are 51543 tetrahedral cells in this mesh.
First 5 tetrahedral cells of the mesh: 
[[4543 4544 1702 1234]
 [4545 4546 4547 4548]
 [4549 4550 4551 4552]
 [4553  346 1009 1019]
 [4554 4025 3968 3857]] 

Feature name: Vitesse / Feature shape: (10682, 3)
Feature name: Pression / Feature shape: (10682,)


In [ ]:
# print(type(meshes))
# accessing_mesh_data(meshes[10])

print(meshes[0].points.shape)
print(meshes[0].cells_dict['tetra'].shape)
print(meshes[0].point_data["Vitesse"].shape)
print(meshes[0].point_data["Pression"].shape)

(10682, 3)
(51543, 4)
(10682, 3)
(10682,)


In [ ]:

meshes[0].points

array([[-0.4082757 ,  9.047513  , -1.452742  ],
       [-0.49194214,  8.805198  , -1.5316691 ],
       [-0.58255124,  8.53299   , -1.5674353 ],
       ...,
       [-0.48404792,  5.647038  ,  1.0676627 ],
       [-3.3310409 ,  6.0282717 , -0.02785564],
       [-0.2818084 ,  6.812995  ,  0.4719045 ]], dtype=float32)

In [ ]:

print(meshes[0].point_data["Vitesse"])

[[-2.9617015e-14 -9.2768124e-15 -1.4815108e-15]
 [-3.6447612e-15 -3.5913130e-15 -3.8873645e-16]
 [-7.1755303e-15 -1.9960418e-14 -1.9002331e-15]
 ...
 [ 2.9312454e+02  2.0616537e+01 -3.6360329e+01]
 [ 2.7642889e+02  2.5440704e+02 -1.3154695e+00]
 [ 2.5838040e+02  4.8682987e+01 -4.1221623e+00]]


In [ ]:
len(meshes)
meshes[0].points
print(meshes[0].point_data["Pression"])
import plotly.express as px
fig = px.histogram(meshes[0].point_data["Pression"], nbins=100)
fig.show()


[203.11459351 202.97369385 202.72950745 ... 162.30140686 189.18040466
 179.61779785]


In [ ]:
import plotly.express as px
fig = px.histogram(meshes[0].point_data["Vitesse"], nbins=100)
fig.show()

In [ ]:


print("\n### DEMO  VTU FILE FORMAT ###")
mock_mesh = create_mock_mesh()
vtu_path = osp.join(os.getcwd(), "mock_mesh.vtu")
mesh_to_vtu(mock_mesh, vtu_path)


### DEMO  VTU FILE FORMAT ###
Mock mesh created.
Mesh saved to /content/mock_mesh.vtu


In [ ]:
meshes[0].points

array([[-0.4082757 ,  9.047513  , -1.452742  ],
       [-0.49194214,  8.805198  , -1.5316691 ],
       [-0.58255124,  8.53299   , -1.5674353 ],
       ...,
       [-0.48404792,  5.647038  ,  1.0676627 ],
       [-3.3310409 ,  6.0282717 , -0.02785564],
       [-0.2818084 ,  6.812995  ,  0.4719045 ]], dtype=float32)

In [ ]:
import plotly.graph_objects as go
import numpy as np
meshes[0].points
x = meshes[0].points[:,0]
y = meshes[0].points[:,1]
z = meshes[0].points[:,2]
fig = go.Figure(data=[go.Mesh3d(x=x, y=y, z=z, color='lightpink', opacity=0.50)])
fig.show()




In [ ]:
mesh0 = meshes[0]

In [ ]:
mesh0.cells_dict['tetra']



array([[4543, 4544, 1702, 1234],
       [4545, 4546, 4547, 4548],
       [4549, 4550, 4551, 4552],
       ...,
       [7026, 9757, 6616, 4818],
       [7026, 4818, 9754, 9756],
       [7026, 7464, 7803, 6272]])

In [ ]:
mesh0.points


array([[-0.4082757 ,  9.047513  , -1.452742  ],
       [-0.49194214,  8.805198  , -1.5316691 ],
       [-0.58255124,  8.53299   , -1.5674353 ],
       ...,
       [-0.48404792,  5.647038  ,  1.0676627 ],
       [-3.3310409 ,  6.0282717 , -0.02785564],
       [-0.2818084 ,  6.812995  ,  0.4719045 ]], dtype=float32)

In [ ]:
# scatter_points
# to draw the scatter plot well, you need to place all of the points but also draw the vertices between them in the right order
# so a point must be next to his neighbors
neighbors = mesh0.cells_dict['tetra']
points = mesh0.points

print(neighbors)
x = np.array([0, 1, 0,0,1])
y = np.array([0,0,1,0,1])
z = np.array([0,0,0,1,0])
mesh0.cells_dict['tetra']
neighbors1 = neighbors[0]




[[4543 4544 1702 1234]
 [4545 4546 4547 4548]
 [4549 4550 4551 4552]
 ...
 [7026 9757 6616 4818]
 [7026 4818 9754 9756]
 [7026 7464 7803 6272]]


In [ ]:

# print(mesh0.point_data["Pression"].shape)
# print(mesh0.points.shape)




In [ ]:
import plotly.graph_objects as go
import numpy as np
from typing import Literal

def plot_tetrahedra(points, neighbors,  color_arr : np.ndarray, mode: Literal['velocity', 'pressure'] = 'pressure'):

    """
    Plot tetrahedra using Plotly.

    Parameters:
    points: numpy array of shape (N, 3) containing point coordinates
    neighbors: numpy array of shape (M, 4) containing point indices for each tetrahedron
    """
    # These are the edges we need to draw for each tetrahedron
    edge_pairs = [
        (0,1), (0,2), (0,3),  # from vertex 0 to all others
        (1,2), (1,3),         # from vertex 1 to remaining
        (2,3)                 # last edge
    ]

    # Initialize lists for the coordinates
    x_coords = []
    y_coords = []
    z_coords = []

    # For each tetrahedron
    for tetra in neighbors:
        # For each edge in the tetrahedron
        for start_idx, end_idx in edge_pairs:
            # Get the actual point indices for this edge
            start_point = points[tetra[start_idx]]
            end_point = points[tetra[end_idx]]

            # Add the coordinates of the line (including None for separation)
            x_coords.extend([start_point[0], end_point[0], None])
            y_coords.extend([start_point[1], end_point[1], None])
            z_coords.extend([start_point[2], end_point[2], None])

    # Create the plot
    print(f"input color arr shape {color_arr.shape}")
    if mode == 'velocity':
        color_arr = np.linalg.norm(color_arr, axis = 1)

    fig = go.Figure(data=[
        go.Scatter3d(
            x=points[:,0],
            y=points[:,1],
            z=points[:,2],
            mode='markers',
            marker=dict(
                size=4,
                color=color_arr,
                colorscale='RdBu',  # Choose your preferred colorscale
                colorbar=dict(
                    title='Pressure',  # Title for the colorbar
                    thickness=20,      # Width of the colorbar
                    x=1.1,            # Position the colorbar to the right
                    len=0.8           # Length of colorbar relative to plot height
                ),
                showscale=True        # This is crucial - shows the colorbar
            ),
            name='Vertices'
        )
    ])


    # Update the layout
    fig.update_layout(
        scene=dict(
            aspectmode='data',
            xaxis_title='X',
            yaxis_title='Y',
            zaxis_title='Z'
        ),
        margin = dict(r = 80),
        showlegend=True,
        title='Tetrahedral Mesh'
    )

    fig.show()

# Usage example:
pressures = mesh0.point_data["Pression"].flatten()
speeds = np.linalg.norm(mesh0.point_data["Vitesse"], axis=1)
plot_tetrahedra(points, neighbors, pressures)

input color arr shape (10682,)


In [ ]:
mesh_t = meshes[40]
points = mesh_t.points
neighbors = mesh_t.cells_dict['tetra']
pressures = mesh_t.point_data["Pression"].flatten()
plot_tetrahedra(points, neighbors, pressures )

input color arr shape (10682,)


In [ ]:
mesh_t = meshes[10]
points = mesh_t.points
neighbors = mesh_t.cells_dict['tetra']
pressures = mesh_t.point_data["Pression"].flatten()
plot_tetrahedra(points, neighbors, pressures )

input color arr shape (10682,)


In [ ]:
mesh_t = meshes[20]
points = mesh_t.points
neighbors = mesh_t.cells_dict['tetra']
pressures = mesh_t.point_data["Pression"].flatten()
plot_tetrahedra(points, neighbors, pressures )

input color arr shape (10682,)


In [ ]:
mesh_t = meshes[30]
points = mesh_t.points
neighbors = mesh_t.cells_dict['tetra']
pressures = mesh_t.point_data["Pression"].flatten()
plot_tetrahedra(points, neighbors, pressures )

input color arr shape (10682,)


In [ ]:
mesh_t = meshes[40]
points = mesh_t.points
neighbors = mesh_t.cells_dict['tetra']
pressures = mesh_t.point_data["Pression"].flatten()
plot_tetrahedra(points, neighbors, pressures )

input color arr shape (10682,)


In [ ]:
mesh_t = meshes[50]
points = mesh_t.points
neighbors = mesh_t.cells_dict['tetra']
pressures = mesh_t.point_data["Pression"].flatten()
plot_tetrahedra(points, neighbors, pressures )

input color arr shape (10682,)
